https://hub.xpub.nl/soupboat/~mirischoeb/api/

https://hub.xpub.nl/soupboat/~mirischoeb/api/iterate/

# cleaning-sewing-mending quill

this tool includes two functions that intervene on text by replacing specific targeted words with either other words or single characters.
The 2 main functions are based in a very simple mechanism, but the scope and results one could get by using them in different ways and with different intentions can be very compelling.
One could break down the meaning of a text, by exposing its structure, taking out specific and meaningful words and detaching such text from its original context.
If then, these words would be substituted for others, the text can be given a new meaning, reclaiming concepts or ideas.
The words could be also erased and replaced for blank spaces in order to create a new narrative meaning with what is left on the page, as well as to create abstract compositions. 
This tool offers a broad spectrum of possibilities in which it can be used, from a very political and subversive use, to a more playful and artistic (or poetic) one.

In [87]:
from flask import Flask, request, json, render_template, url_for
from jinja2 import Environment, PackageLoader, select_autoescape
from weasyprint import HTML, CSS
from nltk.tokenize import word_tokenize

import os 
import json

### functions

In [ ]:
# function: replace, swap
# '''replace all the occurrences of a targeted word in a given text'''
# def swap(text, target, replacement):
#     result = text.replace(target, replacement)
#     return result
def swap(text, target, replacement):
    target = target.lower()
    txt = word_tokenize(text)
    new = []
    
    print(f"swap target:'{target}'")
    for w in txt:
        if w == target:
            w = replacement
            new = new + [w]
        elif w == target[0:1].upper() + target[1:]:
            w = replacement[0:1].upper() + replacement[1:] 
            new = new + [w]
        elif w == target.upper():
            w = replacement.upper()
            new = new + [w]
        else:
            new = new + [w]
    text = ' '.join(new)
    final= text.replace(' .','.').replace(' ,',',').replace(' :',':').replace(' ;',';').replace('< ','<').replace(' >','>').replace(' / ','/').replace('& ','&')
    return final

# function: stitch, mend
# '''replace all the occurrences of a target word with a single character that is repeated as many times as the length of the target'''
## example: stitch('halo stitch this', 'this', '*') ----> result:'halo stitch ****'
def mend(text, target, replacement):
    target = target.lower()
    txt = word_tokenize(text)
    new = []
    
    for w in txt:
        if w == target:
            w = len(w)*replacement
            new = new + [w]
        elif w == target[0].upper() + target[1:]:
            w = len(w)*replacement
            new = new + [w]
        elif w== target.upper():
            w = len(w)*replacement 
            new = new + [w]
        else:
            new = new + [w]
    text = ' '.join(new)
    final= text.replace(' .','.').replace(' ,',',').replace(' :',':').replace(' ;',';').replace('< ','<').replace(' >','>').replace(' / ','/').replace('& ','&')
    return final

# pop or highlight 
def underline(text,Group):
    txt = word_tokenize(text)
    
    txt_linebr = []
    for token in txt:
        if token == '<':
            continue
        elif token == 'br/':
            token='<br/>'
            txt_linebr.append(token)
        elif token == '>':
            continue
        else:
            txt_linebr.append(token)
    print(txt_linebr)     
    new = []
    group = Group.split(",")
    for w in txt_linebr:
        if w=='<br/>':
            new = new + [w]
        elif w not in group:
            w = len(w) * ' '
            new = new + [w]
        elif w in group :
            new = new + [w]
    text = ' '.join(new)
    final= text.replace(' .','.').replace(' ,',',').replace(' :',':').replace(' ;',';').replace('< ','<').replace(' >','>').replace(' / ','/').replace('& ','&')
    return final


#function: txt_br
#to read the line breaks in a .txt file, returns string readable in html 
def txt_br(any_text):
    lines= any_text.readlines()
    replaced = ''
    for line in lines:
        replaced+= line.replace('\n', '<br/>')   
    return replaced

### flask 

In [89]:
!pwd

/home/mirischoeb/public_html/replace


In [ ]:
app = Flask(__name__)


archived = []

@app.route(f"/~mirischoeb/api/")
def replace():
    
    text=request.values.get('text', '')
    target = request.values.get('target', '')
    replacement = request.values.get('replacement', '')
    title = f"<h2>{request.values.get('title', '')}</h2>"
    txt_result = f"<p>{swap(text, target, replacement)}</p>"
    contents= title + txt_result
    
    with open("./assets/outputs/db.txt", "a") as db:
        db.write(contents+ " \n")
        
    with open ("archive_section.html", "a") as output:
        print(contents, file=output)
    
    
    return render_template("index.html",
                          text=text,
                          contents=contents)
    

# generate an archive page, is it better to have it static?
@app.route(f"/~mirischoeb/api/archive/", methods=['GET'])
def archive():
    #read the json file
    with open("archive.json", "r") as file:
            archive_input = json.loads(file.read())
            archive = archive_input['archive']
            sections=[]\
            #create a list with all the sections contents from the j
            for section in archive:
                sections.append(section['contents'])
                
            
#     archived= open ("archive_section.html", "r")
#     contents = archived.read()
    
#     HTML(filename="archive.html").write_pdf('./assets/outputs/replace_booklet.pdf')
        
    return render_template("archive.html",
                           sections = sections)


temp_changes=[]
@app.route("/~mirischoeb/api/iterate/", methods=['GET', 'POST'])

def iterate(): 
    target = request.values.get('target', '')
#     stitch = request.values.get('mend','')
#     replacement = request.values.get('replacement', '')
    f_text = request.values.get('f_text','')
    function = request.values.get('function', 'replace') 
    with open("./assets/corpora/mitsotakis.txt", 'r') as file:
        source = txt_br(file)
        text = request.values.get('text','')
        if function == 'mend': #and not replacement:
            stitch = f_text
            if ' ' in stitch:
                space = stitch.replace(' ','&nbsp;')
                result= mend(text, target, space)
            else:
                result= mend(text, target, stitch)
        else:
            replacement = f_text
            result = swap(text, target, replacement)
        
        # now save temporary all the changes in the list changes
        temp_changes.append(result)
        
    if not text:
        # the first time we open the url the text is not saved, so plz flask, use the original source as text!
#         if stitch and not replacement:
        if function == 'mend':
            
            result = mend(source, target, f_text)
        else:
            result = swap(source, target, f_text)
        
        # when we wanto to save the changes to the archive, we use another form-button with method='POST':
        #if the save button is pressed:
        #save the last change non empty change in the archive and clear the temporary list "changes"
    if request.method == 'POST':
        with open("archive.json", "r") as file:
            archive_input = json.loads(file.read())
            archive = archive_input['archive']
            i = len(temp_changes)-1
            while i >= 0:
                last_change = temp_changes[i]
                if last_change:
                    break
                else:
                    i -= 1
            section = {"title":'', 
                       "contents": last_change}
            archive.append(section)
        #print to the archive    
        with open("archive.json", "w") as file:
            file.write(json.dumps({"archive":archive}))
            
        #print with the line printer 
        with open('/dev/usb/lp0', 'w') as lp:
            print(last_change, file=lp)

        temp_changes.clear()
           
    return render_template('iterate.html', text=text, result=result, source= source, function=function, f_text=f_text)
        
        
        
        
        
#     target = request.values.get('target', '')
#     replacement = request.values.get('replacement', '')
#     with open("./assets/mitsotakis.txt", 'r') as file:
#         source = txt_br(file)
#         text = request.values.get('text','')
#         result = swap(text, target, replacement)
#     if not text:
#         result = swap(source, target, replacement)
#     return render_template('iterate.html', text=text, result=result, source= source)



app.run(port=9089)

 * Serving Flask app '__main__' (lazy loading)
 * Environment: production
   Use a production WSGI server instead.
 * Debug mode: off


 * Running on http://127.0.0.1:9089/ (Press CTRL+C to quit)
127.0.0.1 - - [14/Dec/2021 17:13:14] "GET /~mirischoeb/api/ HTTP/1.0" 200 -


swap target:''


127.0.0.1 - - [14/Dec/2021 17:13:16] "GET /~mirischoeb/api/iterate/ HTTP/1.0" 200 -


swap target:''
swap target:''


127.0.0.1 - - [14/Dec/2021 17:15:11] "GET /~mirischoeb/api/iterate/ HTTP/1.0" 200 -


swap target:''
swap target:''


127.0.0.1 - - [14/Dec/2021 17:15:45] "GET /~mirischoeb/api/ HTTP/1.0" 200 -


swap target:''


127.0.0.1 - - [14/Dec/2021 17:16:04] "GET /~mirischoeb/api/archive/ HTTP/1.0" 200 -
127.0.0.1 - - [14/Dec/2021 17:16:04] "GET /~mirischoeb/api/archive/style.css HTTP/1.0" 404 -


In [ ]:
''[0]


# 

## teeeeeesstttssssss

In [ ]:
from weasyprint import HTML, CSS

# with is nice cause it auto-closes the file once "outside" the with block
with open ("test.html", "a") as output:
    print ("<pre>", file=output)
    print (sent + " ", file=output)
    print ("</pre>", file=output)
HTML(filename="test.html").write_pdf('./test.pdf')

In [ ]:
def ifcap(text, target, replacement):
    result=[]
    index= 0
    for w in text.split():
        w_lower = w.lower()
        if w_lower == target and w.isupper()==true:
            while w[index].isupper() == true and index<len(w):
                change=''
                for l in replacement:
                    change= l.upper()
                index +=1
            result += [w_lower.replace(target, replacement)]
    print(result)

In [ ]:
def ifcap(text, target, replacement):
    result=[]
    index= 0
    for w in text.split():
        w_lower = w.lower()
        change=''
        if w_lower == target:
            
            while index < len(w):
                print('oo')
#                 if str(w[index]).isupper() == true:
#                     change+= str(replacement[index]).upper()
#                     print (change)
#                 else:
#                     change+= replacement[index]
                index+=1
        result += [w_lower.replace(target, change)]
    print(result)

In [ ]:
ifcap('Capital and capital', 'c', 'CC')

In [ ]:
word ='ciao'
print(len(word))

In [ ]:
with open("./assets/corpora/mitsotakis.txt", 'r') as source:
    print(source)

In [ ]:
sentence= "stitches //Have something <\repairing\ have HAVE"

In [ ]:
# stitch function, replace a target with stitches

def change(text, target, replacement):
    result = text.replace(target, replacement)
    return result

In [ ]:
mend(sentence, 'have', ' ')

## Printing receipts:

In [ ]:

with open('/dev/usb/lp0', 'w') as lp:
        print("""
            

   
            
            
            """, file=lp)